In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
from zipfile import ZipFile
file_name = "/content/drive/MyDrive/Datasets/Arabic_Hand_Written_Dataset.zip"
with ZipFile(file_name, 'r') as zip:
  zip.extractall()
  print('finish')  #just to show that file is unzipped

# ###### Importing Important Libraries

In [ ]:
import tensorflow as tf                                                         
import numpy as np                                                              
import pandas as pd                                                             
import cv2    
from sklearn.metrics import confusion_matrix
%matplotlib inline
from sklearn.metrics import accuracy_score
import matplotlib.image  as mpimg
import matplotlib.pyplot as plt                                                        
from matplotlib import pyplot as plt                                            
from tensorflow.keras.utils import to_categorical  
from sklearn.utils import shuffle  
from tensorflow.keras.models import Sequential
from tensorflow.keras.callbacks import ModelCheckpoint                                     
from tensorflow.keras.layers import Conv2D, MaxPooling2D, GlobalAveragePooling2D, BatchNormalization, Dropout, Dense, Flatten
from sklearn.metrics import roc_auc_score
import seaborn as sns
%%capture
from sklearn.metrics import classification_report
from sklearn import metrics
from sklearn.metrics import roc_curve
import matplotlib.image  as mpimg
import matplotlib.pyplot as plt

In [ ]:
train_data_x= pd.read_csv("/content/Arabic_Hand_Written_Dataset/csvTrainImages 13440x1024.csv")
train_data_y= pd.read_csv("/content/Arabic_Hand_Written_Dataset/csvTrainLabel 13440x1.csv")
test_data_x= pd.read_csv("/content/Arabic_Hand_Written_Dataset/csvTestImages 3360x1024.csv")
test_data_y= pd.read_csv("/content/Arabic_Hand_Written_Dataset/csvTestLabel 3360x1.csv")

In [ ]:
#### Pixels

In [ ]:
print('We have  %d training images each contains %d pixels.' %(train_data_x.shape[0], train_data_x.shape[1]))
####print('We have  %d training labels each contains %d classes.' %(train_data_y.shape[0], len(train_data_y.value_counts())))
####print('We have  %d training labels each contains %d classes.' %(train_data_y.shape[0], len(train_data_y.value_counts())))
print('We have  %d training labels each contains %d classes.' %(train_data_y.shape[0], len(train_data_y.value_counts())))
####print('We have  %d training labels each contains %d classes.' %(train_data_y.shape[0], len(train_data_y.value_counts())))
print('We have  %d testing images each contains %d pixels.' %(test_data_x.shape[0], test_data_x.shape[1]))
print('We have  %d testing labels each contains %d classes.' %(test_data_y.shape[0], len(test_data_y.value_counts())))

In [ ]:
####Dimensions /example

In [ ]:
fig = plt.figure(figsize=(8, 8))                   
columns = 4                                                                     
rows = 5      
####for i in range(1, columns*rows +1):                                                                  
for i in range(1, columns*rows +1):                                             
  img = test_data_x.iloc[i].to_numpy().reshape((32,32))                         
  fig.add_subplot(rows, columns, i)                                             
  plt.imshow(img, cmap='gray')                                                  
plt.show() 

In [ ]:
def preprocess_data(train_data_x):
  train_data_x = train_data_x.to_numpy().reshape((train_data_x.shape[0], 32, 32)).astype('uint8')  ##numpy operation/////
  for i in range(len(train_data_x)):
    train_data_x[i] = cv2.rotate(train_data_x[i], cv2.ROTATE_90_CLOCKWISE)      
    train_data_x[i] = np.flip(train_data_x[i], 1)                               
  train_data_x = train_data_x.reshape([-1, 32, 32, 1]).astype('uint8')          
  train_data_x = train_data_x.astype('float32')/255                             
  return np.asarray(train_data_x)

In [ ]:
train_x = preprocess_data(train_data_x)                                         
test_x = preprocess_data(test_data_x)                                           

In [ ]:
train_y = to_categorical(train_data_y.values.astype('int32') - 1, num_classes=28)  ###To categorical
test_y = to_categorical(test_data_y.values.astype('int32') - 1, num_classes=28)

In [ ]:
train_x, train_y = shuffle(train_x, train_y)                                    
test_x, test_y, shuffle(test_x, test_y)                                         

In [ ]:
def create_model(activation='relu', optimizer='adam', kernel_initializer='he_normal'):
    
    model = Sequential()

    model.add(Conv2D(32, (3,3), padding='same', input_shape=(32, 32, 1), activation= activation, kernel_initializer=kernel_initializer))
    model.add(MaxPooling2D(2,2))
    model.add(Dropout(0.2))
    model.add(BatchNormalization())
    

    model.add(Conv2D(64, (3,3), padding='same', activation= activation, kernel_initializer=kernel_initializer))
    model.add(MaxPooling2D(2,2))
    model.add(Dropout(0.2))
    model.add(BatchNormalization())
    

    model.add(Conv2D(128, (3,3), padding='same', activation= activation, kernel_initializer=kernel_initializer))
    model.add(MaxPooling2D(2,2))
    model.add(Dropout(0.2))
    model.add(BatchNormalization())
    

    model.add(Flatten())
    model.add(Dense(32, activation= activation, kernel_initializer=kernel_initializer, kernel_regularizer='l2'))
    model.add(Dropout(0.2))
    model.add(BatchNormalization())
    

    model.add(Dense(28, activation='softmax'))

    model.compile(optimizer=optimizer,
                    loss='categorical_crossentropy',
                    metrics=['accuracy'])
    return model

In [ ]:
model = create_model()                                                          
model.summary()                                                                 

In [ ]:

model = create_model(optimizer='adam',                                       
                     kernel_initializer='uniform',
                     activation='relu')

In [ ]:
checkpointer = ModelCheckpoint(filepath='weights.hdf5', verbose=1, save_best_only=True)
history = model.fit(train_x,                                                    
                    train_y, 
                    validation_split= 0.3,                                      
                    epochs=50,                   #### 50 iterations                               
                    batch_size=50,               #### 50 batches                  
                    callbacks=[checkpointer])                                   

Training Accuracy

In [ ]:
model.load_weights('weights.hdf5')                                                     
model.evaluate(train_x, train_y)   

Testing Performnce

In [ ]:
model.load_weights('weights.hdf5')                                                      
model.evaluate(test_x, test_y)   

**Testing model on unseen data**

In [ ]:
test_x, test_y = shuffle(test_x, test_y, random_state=30)
test_y = test_y[:10]
test_x = test_x[:10]
print('Arabic alphabet:')
print("ي و ه ن م ل ك ق ف غ ع ظ ط ض ص ش س ز ر ذ د خ ح ج ث ت ب ا\n0 1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27")
print()
pred = model.predict(test_x)
outputDf = pd.DataFrame(pred)
predictedIndex = list(outputDf.idxmax(axis=1))
print("Predicted index: ", predictedIndex)
print()
test_y = pd.DataFrame(test_y)
realIndex = list(test_y.idxmax(axis=1))
print("Real index: ", realIndex)
for i in range(len(test_x)):
    real = realIndex[i]
    predicted = predictedIndex[i]
    plt.title(f'Actual: {real}    predicted: {predicted}')
    img = test_x[i]
    img = cv.rotate(img, cv.ROTATE_90_CLOCKWISE)
    plt.imshow(img,cmap='gray')
    plt.show() 

In [ ]:
pred_y = model.predict(test_x)
pred_y=np.argmax(pred_y, axis=1)
test_y=np.argmax(test_y, axis=1)

In [ ]:
accuracy_score(test_y, pred_y)

In [ ]:
# LOSS VS ACCURACY

acc=history.history['accuracy']
val_acc=history.history['val_accuracy']
loss=history.history['loss']
val_loss=history.history['val_loss']
epochs=range(len(acc)) 
plt.plot(history.history['accuracy'])
plt.plot(history.history['val_accuracy'])
plt.title('Training and validation accuracy')
plt.legend(['training accuracy', 'validation accuracy'], loc='lower right')
plt.ylabel('accuracy')
plt.xlabel('epoch')
plt.figure()


plt.plot(history.history['loss'])
plt.plot(history.history['val_loss'])
plt.title('Training and validation loss')
plt.legend(['training loss', 'validation loss'], loc=' upper right')
plt.ylabel('loss')
plt.xlabel('epoch')


plt.title('Training and validation loss')

In [ ]:
cm = confusion_matrix(test_y, pred_y)
cm

In [ ]:
sns.heatmap(cm,annot=True)
#plt.subplots(1,1,figsize=(14,7))
plt.savefig('h.png')

In [ ]:
fig,ax=plt.subplots(1,1,figsize=(10,10))
sns.heatmap(confusion_matrix(test_y, pred_y),annot=True)


plt.show()

In [ ]:
print("Classification Report: \n", classification_report(test_y, pred_y))

In [ ]:
y_pred_prob = model.predict(test_x)[:, 1]

fpr, tpr, thresholds = metrics.roc_curve(test_y, y_pred_prob, pos_label = 1)
plt.plot(fpr, tpr)
plt.xlim([0.0, 1.0])
plt.ylim([0.0, 1.0])
plt.title('ROC curve classifier')
plt.xlabel('False Positive Rate (FPR)')
plt.ylabel('True Positive Rate (TPR)')

In [ ]:
fpr = {}
tpr = {}
thresh ={}

n_class = 28

for i in range(n_class):    
    fpr[i], tpr[i], thresh[i] = roc_curve(test_y, y_pred_prob, pos_label = i)
plt.plot(fpr[0], tpr[0], linestyle='--',color='orange', label='أ')
plt.plot(fpr[1], tpr[1], linestyle='--',color='green', label='ب')
plt.plot(fpr[2], tpr[2], linestyle='--',color='blue', label='ت')
plt.plot(fpr[3], tpr[3], linestyle='--',color='yellow', label='ث')
plt.plot(fpr[4], tpr[4], linestyle='--',color='purple', label='ج')
plt.plot(fpr[5], tpr[5], linestyle='--',color='lime', label='ح')
plt.plot(fpr[6], tpr[6], linestyle='--',color='chocolate', label='خ')
plt.plot(fpr[7], tpr[7], linestyle='--',color='black', label='د')
plt.plot(fpr[8], tpr[8], linestyle='--',color='grey', label='ذ')
plt.plot(fpr[9], tpr[9], linestyle='--',color='red', label='ر')
plt.plot(fpr[10], tpr[10], linestyle='--',color='navy', label='ز')
plt.plot(fpr[11], tpr[11], linestyle='--',color='gold', label='س')
plt.plot(fpr[12], tpr[12], linestyle='--',color='orchid', label='ش')
plt.plot(fpr[13], tpr[13], linestyle='--',color='olive', label='ص')
plt.plot(fpr[14], tpr[14], linestyle='--',color='pink', label='ض')
plt.plot(fpr[15], tpr[15], linestyle='--',color='silver', label='ط')
plt.plot(fpr[16], tpr[16], linestyle='--',color='tan', label='ظ')
plt.plot(fpr[17], tpr[17], linestyle='--',color='aqua', label='ع')
plt.plot(fpr[18], tpr[18], linestyle='--',color='indigo', label='غ')
plt.plot(fpr[19], tpr[19], linestyle='--',color='ivory', label='ف')
plt.plot(fpr[20], tpr[20], linestyle='--',color='maroon', label='ق')
plt.plot(fpr[21], tpr[21], linestyle='--',color='brown', label='ك')
plt.plot(fpr[22], tpr[22], linestyle='--',color='plum', label='ل')
plt.plot(fpr[23], tpr[23], linestyle='--',color='yellow', label='م')
plt.plot(fpr[24], tpr[24], linestyle='--',color='teal', label='ن')
plt.plot(fpr[25], tpr[25], linestyle='--',color='azure', label='ه')
plt.plot(fpr[26], tpr[26], linestyle='--',color='beige', label='و')
plt.plot(fpr[27], tpr[27], linestyle='--',color='red', label='ى')
plt.title('Multiclass ROC curve')
plt.xlabel('False Positive Rate')
plt.ylabel('True Positive rate')
plt.legend(loc='lower right')
plt.savefig('Multiclass ROC');

In [ ]:
pred_y = model.predict(test_x)

In [ ]:
roc_auc_score(test_y, pred_y, multi_class='ovr')

In [ ]:


acc=history.history['accuracy']
val_acc=history.history['val_accuracy']
loss=history.history['loss']
val_loss=history.history['val_loss']

epochs=range(len(acc)) 


plt.plot(history.history['accuracy'])
plt.plot(history.history['val_accuracy'])
plt.title('Training and validation accuracy')
plt.legend(['training accuracy', 'validation accuracy'], loc='lower right')
plt.ylabel('accuracy')
plt.xlabel('epoch')
plt.figure()


plt.plot(history.history['loss'])
plt.plot(history.history['val_loss'])
plt.title('Training and Testing loss')
plt.legend(['training loss', 'validation loss'], loc=' upper right')
plt.ylabel('loss')
plt.xlabel('epoch')

####Plot tilte 
plt.title('Training and validation loss')